In [9]:
from controllables.energyplus import System

system = System(
            building='all_room_have_hvac_t_22.idf',
            weather='SGP_Singapore_486980_IWEC.epw',
            # TODO
            report='tmp/',
            repeat=True,
        )
        #system.add('logging:progress')

system.add('logging:progress').start()

  0%|          | 0/100 [00:00<?, ?it/s]

System({'building': 'all_room_have_hvac_t_22.idf', 'weather': 'SGP_Singapore_486980_IWEC.epw', 'report': 'tmp/', 'repeat': True})

In [10]:
system.variables.available_keys()

In [11]:
from controllables.core import TemporaryUnavailableError
from controllables.energyplus import (
    Actuator, 
    OutputVariable,
    OutputMeter
)
import pythermalcomfort as pytc
import numpy as _numpy_
from controllables.core import Variable, BaseVariable
import itables as _itables_

In [12]:
class PMVVariable(BaseVariable):
        def __init__(
            self, 
            tdb: BaseVariable,
            tr: BaseVariable,
            rh: BaseVariable,
            metab_rate=1.5, clothing=.5, pmv_limit=.5,
        ):
            self.tdb = tdb
            self.tr = tr
            self.rh = rh
            self._metab_rate = _numpy_.asarray(metab_rate)
            self._clothing = _numpy_.asarray(clothing)
            self._pmv_limit = _numpy_.asarray(pmv_limit)
        
        @property
        def value(self):
            res = pytc.models.pmv_ppd(
                tdb=self.tdb.value, 
                tr=self.tr.value, 
                # calculate relative air speed
                vr=pytc.utilities.v_relative(v=0.1, met=self._metab_rate), 
                rh=self.rh.value, 
                met=self._metab_rate, 
                # calculate dynamic clothing
                clo=pytc.utilities.clo_dynamic(clo=self._clothing, met=self._metab_rate),
                limit_inputs=False ,
            )['pmv']

            return res


In [13]:
from controllables.core.tools.records import VariableRecords
tdb = system[OutputVariable.Ref('Zone Mean Air Temperature','1FFIRSTFLOORWEST:OPENOFFICE')]
tr = system[OutputVariable.Ref('Zone Mean Radiant Temperature','1FFIRSTFLOORWEST:OPENOFFICE')]
rh = system[OutputVariable.Ref('Zone Air Relative Humidity','1FFIRSTFLOORWEST:OPENOFFICE')]

pmv= PMVVariable(tdb, tr, rh)
records = VariableRecords({
    '🕰️': system['wallclock:calendar'],
    # 'Electricity:Facility': 
    #     system[OutputMeter.Ref('Electricity:Facility')],
    'elec':system[OutputMeter.Ref('Electricity:HVAC')],
    'temp':system[OutputVariable.Ref('Zone Mean Air Temperature','1FFIRSTFLOORWEST:OPENOFFICE')],
    'pmv':pmv,
    # 'pmv_system':system[OutputVariable.Ref('Zone Thermal Comfort Fanger Model PMV','PEOPLE 1FFIRSTFLOORWEST:OPENOFFICE')],
    'occupancy':system[OutputVariable.Ref('Schedule Value','Office_OpenOff_Occ')]
},maxlen = 10000).watch(system.events['timestep'])

/home/AD/user/lab/reports/2024xxxx/.venv/lib/python3.11/site-packages/controllables/energyplus/variables.py:370: RuntimeWarning: OutputVariable(OutputVariable.Ref(type='Zone Mean Air Temperature', key='1FFIRSTFLOORWEST:OPENOFFICE')) requested while Kernel() is running; It may not be available until the next run. More info: https://energyplus.readthedocs.io/en/latest/datatransfer.html#datatransfer.DataExchange.request_variable
  _warnings_.warn(
/home/AD/user/lab/reports/2024xxxx/.venv/lib/python3.11/site-packages/controllables/energyplus/variables.py:370: RuntimeWarning: OutputVariable(OutputVariable.Ref(type='Zone Mean Radiant Temperature', key='1FFIRSTFLOORWEST:OPENOFFICE')) requested while Kernel() is running; It may not be available until the next run. More info: https://energyplus.readthedocs.io/en/latest/datatransfer.html#datatransfer.DataExchange.request_variable
  _warnings_.warn(
/home/AD/user/lab/reports/2024xxxx/.venv/lib/python3.11/site-packages/controllables/energyplus/var

In [14]:
df = records.dataframe()
df.to_csv('tmp/records_baseline_t_22.csv', index=False)
_itables_.show(df)

In [7]:
df.describe()

elec        temp         pmv
count  2.300000e+02  230.000000  230.000000
mean   1.006406e+07   22.757197   -0.005478
std    1.256029e+06    1.103861    0.372176
min    9.067028e+06   20.312597   -0.780000
25%    9.067028e+06   21.932421   -0.320000
50%    9.201642e+06   23.495475    0.130000
75%    1.091504e+07   23.496206    0.320000
max    1.335827e+07   24.349195    0.400000

In [18]:
import pandas
train = pandas.read_csv("tmp/records_single.csv")
train['🕰️'] = pandas.to_datetime(train['🕰️'])
_itables_.show(train)

In [19]:
train.describe()

🕰️           pmv  AHU COOLING COIL
count                          36864  36864.000000      36864.000000
mean   2002-07-17 00:08:25.202966016     -0.361850     104020.242623
min              2002-01-01 00:00:00     -1.230000      61320.604462
25%              2002-07-09 00:10:00     -0.620000      87008.601593
50%              2002-07-17 00:10:00     -0.310000      94517.785299
75%              2002-07-25 00:10:00     -0.090000     121222.399098
max              2002-08-02 00:00:00      0.570000     174996.840643
std                              NaN      0.315945      24294.228637

In [23]:
import plotly

fig = plotly.graph_objs.Figure()
fig.add_scatter(x=df['🕰️'], y=df['pmv'], name='Baseline')
fig.add_scatter(x=train['🕰️'], y=train['pmv'], name='TODO')
fig

In [22]:
import plotly.express as px

px.scatter(x=df['🕰️'], y=df['pmv'], title='Baseline')
px.scatter(x=train['🕰️'], y=train['pmv'], title='TODO')
